In [1]:
import os
import sys
module_path = os.path.abspath(os.path.join('../../..'))
if module_path not in sys.path:
    sys.path.append(module_path)

In [2]:
print(module_path)

/Users/revilooliver/Documents/quantum_computing/research/pauli_sandwitching/cut4mitigation


In [3]:
# author: Ji Liu email: ji.liu@anl.gov

import itertools, numpy
import circuit_cutter
import mlrecon_methods as ml
import numpy as np
import mthree

import qiskit
from qiskit import *
from qiskit import QuantumCircuit, QuantumRegister, ClassicalRegister, Aer, execute, transpile

from qiskit.transpiler import PassManager

from qiskit.converters import circuit_to_dag
from qiskit.visualization import dag_drawer, plot_histogram
from qiskit.compiler import assemble

from qiskit.tools.monitor import job_monitor, backend_monitor, backend_overview

import qiskit.providers.aer.noise as noise
from qiskit.providers.aer.noise import NoiseModel

from utils.utils import filter_results, dict_to_list, H_distance, total_counts, norm_dict
from utils.vqe_utils import read_from_file, MeasureCircuit, find_commute_groups, evaluation, apply_checking_circuit
from mlrecon_methods import run_circuits, collect_fragment_circuits

In [4]:
qiskit.__qiskit_version__

{'qiskit-terra': '0.22.2', 'qiskit-aer': '0.11.1', 'qiskit-ignis': '0.7.1', 'qiskit-ibmq-provider': '0.19.2', 'qiskit': '0.39.2', 'qiskit-nature': '0.5.1', 'qiskit-finance': None, 'qiskit-optimization': None, 'qiskit-machine-learning': None}

In [5]:
numpy.set_printoptions(linewidth = 200)

simulation_backend = "qasm_simulator"

In [6]:
IBMQ.load_account()
provider = IBMQ.get_provider(hub='ibm-q-ornl', group='ornl', project='chm185')
provider.backends()

[<IBMQSimulator('ibmq_qasm_simulator') from IBMQ(hub='ibm-q-ornl', group='ornl', project='chm185')>,
 <IBMQBackend('ibmq_montreal') from IBMQ(hub='ibm-q-ornl', group='ornl', project='chm185')>,
 <IBMQBackend('ibmq_toronto') from IBMQ(hub='ibm-q-ornl', group='ornl', project='chm185')>,
 <IBMQBackend('ibmq_kolkata') from IBMQ(hub='ibm-q-ornl', group='ornl', project='chm185')>,
 <IBMQBackend('ibmq_mumbai') from IBMQ(hub='ibm-q-ornl', group='ornl', project='chm185')>,
 <IBMQBackend('ibmq_lima') from IBMQ(hub='ibm-q-ornl', group='ornl', project='chm185')>,
 <IBMQBackend('ibmq_belem') from IBMQ(hub='ibm-q-ornl', group='ornl', project='chm185')>,
 <IBMQBackend('ibmq_quito') from IBMQ(hub='ibm-q-ornl', group='ornl', project='chm185')>,
 <IBMQBackend('ibmq_guadalupe') from IBMQ(hub='ibm-q-ornl', group='ornl', project='chm185')>,
 <IBMQSimulator('simulator_statevector') from IBMQ(hub='ibm-q-ornl', group='ornl', project='chm185')>,
 <IBMQSimulator('simulator_mps') from IBMQ(hub='ibm-q-ornl', grou

In [7]:
device = provider.get_backend('ibm_auckland')
device

<IBMQBackend('ibm_auckland') from IBMQ(hub='ibm-q-ornl', group='ornl', project='chm185')>

In [8]:
device.configuration().to_dict()['max_shots']

100000

In [9]:
from qiskit import IBMQ, Aer
from qiskit.providers.aer.noise import NoiseModel
noise_model = NoiseModel.from_backend(device, gate_error = False, thermal_relaxation= False)
print(noise_model)

NoiseModel:
  Basis gates: ['cx', 'id', 'reset', 'rz', 'sx', 'x']
  Instructions with noise: ['measure']
  Qubits with noise: [0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26]
  Specific qubit errors: [('measure', (0,)), ('measure', (1,)), ('measure', (2,)), ('measure', (3,)), ('measure', (4,)), ('measure', (5,)), ('measure', (6,)), ('measure', (7,)), ('measure', (8,)), ('measure', (9,)), ('measure', (10,)), ('measure', (11,)), ('measure', (12,)), ('measure', (13,)), ('measure', (14,)), ('measure', (15,)), ('measure', (16,)), ('measure', (17,)), ('measure', (18,)), ('measure', (19,)), ('measure', (20,)), ('measure', (21,)), ('measure', (22,)), ('measure', (23,)), ('measure', (24,)), ('measure', (25,)), ('measure', (26,))]


In [10]:
noisy_simulator = provider.get_backend('ibmq_qasm_simulator')

In [12]:
front_layer = QuantumCircuit.from_qasm_file("qasm/vqe_HF_front.qasm")

In [13]:
mid_layer = QuantumCircuit.from_qasm_file("qasm/vqe_HF_mid.qasm")

In [14]:
end_layer = QuantumCircuit.from_qasm_file("qasm/vqe_HF_end.qasm")

In [15]:
orign_circuit = front_layer + mid_layer + end_layer

/var/folders/s4/3cvgkkn17hg628pzrzzjnhww0000gn/T/ipykernel_31068/743480212.py:1: DeprecationWarning: The QuantumCircuit.__add__() method is being deprecated.Use the compose() method which is more flexible w.r.t circuit register compatibility.
  orign_circuit = front_layer + mid_layer + end_layer


In [16]:
orign_circuit.draw()

┌───┐        ┌────────────────┐┌────────────┐   ┌────────────────┐»
q_0: ───────┤ X ├────────┤ Ry(6.8272e-06) ├┤ Rz(1.7169) ├─■─┤ Ry(1.7553e-05) ├»
     ┌──────┴───┴──────┐ └─┬────────────┬─┘└────────────┘ │ └────────────────┘»
q_1: ┤ Ry(-1.6337e-05) ├───┤ Rz(1.5283) ├─────────────────■─────────■─────────»
     └──────┬───┬──────┘┌──┴────────────┴─┐┌────────────┐           │         »
q_2: ───────┤ X ├───────┤ Ry(-1.9505e-05) ├┤ Rz(1.8468) ├───────────■─────────»
     ┌──────┴───┴──────┐└──┬────────────┬─┘└────────────┘                     »
q_3: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├─────────────────────────────────────»
     └──────┬───┬──────┘ ┌─┴────────────┴─┐┌───────────┐                      »
q_4: ───────┤ X ├────────┤ Ry(6.1035e-05) ├┤ Rz(1.818) ├──────────────────────»
      ┌─────┴───┴──────┐ └─┬───────────┬──┘└───────────┘                      »
q_5: ─┤ Ry(5.9653e-06) ├───┤ Rz(1.829) ├──────────────────────────────────────»
      └─────┬───┬──────┘ ┌─┴───────────┴──┐┌────────────┐                     »
q_6: ───────┤ X ├────────┤ Ry(9.3127e-06) ├┤ Rz(1.7187) ├─────────────────────»
      ┌─────┴───┴──────┐ ├────────────────┤└────────────┘                     »
q_7: ─┤ Ry(-0.0043765) ├─┤ Rz(0.00058093) ├───────────────────────────────────»
      └────────────────┘ └────────────────┘                                   »
q_8: ─────────────────────────────────────────────────────────────────────────»
                                                                              »
«        ┌────────────┐                                                      »
«q_0: ───┤ Rz(1.5641) ├──────────────────────────────────────────────────────»
«     ┌──┴────────────┴─┐┌─────────────┐                                     »
«q_1: ┤ Ry(-5.2173e-06) ├┤ Rz(0.89072) ├─────────────────────────────────────»
«     └─────────────────┘├─────────────┴┐ ┌─────────────┐                    »
«q_2: ─────────■─────────┤ Ry(2.73e-05) ├─┤ Rz(0.88955) ├────────────────────»
«              │         └──────────────┘┌┴─────────────┴─┐ ┌──────────────┐ »
«q_3: ─────────■────────────────■────────┤ Ry(1.6108e-06) ├─┤ Rz(-0.12592) ├─»
«                               │        └────────────────┘┌┴──────────────┴┐»
«q_4: ──────────────────────────■────────────────■─────────┤ Ry(-8.148e-06) ├»
«                                                │         └────────────────┘»
«q_5: ───────────────────────────────────────────■─────────────────■─────────»
«                                                                  │         »
«q_6: ─────────────────────────────────────────────────────────────■─────────»
«                                                                            »
«q_7: ───────────────────────────────────────────────────────────────────────»
«                                                                            »
«q_8: ───────────────────────────────────────────────────────────────────────»
«                                                                            »
«                                                           
«q_0: ──────────────────────────────────────────────────────
«                                                           
«q_1: ──────────────────────────────────────────────────────
«                                                           
«q_2: ──────────────────────────────────────────────────────
«                                                           
«q_3: ──────────────────────────────────────────────────────
«        ┌────────────┐                                     
«q_4: ───┤ Rz(1.0747) ├─────────────────────────────────────
«     ┌──┴────────────┴─┐  ┌──────────────┐                 
«q_5: ┤ Ry(-8.6542e-06) ├──┤ Rz(-0.21554) ├─────────────────
«     └─────────────────┘┌─┴──────────────┴┐┌─────────────┐ 
«q_6: ─────────■─────────┤ Ry(-8.1451e-06) ├┤ Rz(0.25427) ├─
«              │         └┬────────────────┤├─────────────┴┐
«q_7: ─────────■──────────┤ Ry(-0.0044055) ├┤ Rz(0.010242) ├
«              

In [17]:
#checking circuit

In [18]:
phase_y_front = [6.827165202923369e-06,-1.6337052388981617e-05, -1.9504648473842978e-05, -4.583505307611714e-05, 6.10354282870864e-05, 5.965270087646158e-06, 9.312744374460134e-06, -0.0043764639879769]
phase_z_front = [1.7168697590535538, 1.5283131502120553, 1.8467840590281954, 1.9183949883797635, 1.8180451683566035, 1.8290020607579571,1.7186918294701956 ,0.0005809279491065732 ]
phase_y_end = [1.7553477050418194e-05, -5.2173015630282704e-06, 2.7300161977647244e-05, 1.6108036965651842e-06,-8.147972934398958e-06, -8.65422271101483e-06, -8.145059343430974e-06, -0.0044055233224810164]
phase_z_end = [1.5640736434660867, 0.8907239659216719, 0.8895530769206249, -0.12591739710453853, 1.0747017329581952, -0.21554369415117478, 0.25426734596118483, 0.010241971123548377]
x_front = [True, False, True, False, True, False, True, False]

In [19]:
qubit_id = 3
circuit = QuantumCircuit(9)
apply_checking_circuit(circuit, [qubit_id], [8], side = 'front', phase_y = phase_y_front[qubit_id], phase_z = phase_z_front[qubit_id], x = x_front[qubit_id])
circuit += orign_circuit
apply_checking_circuit(circuit, [qubit_id], [8], side = 'end', phase_y = phase_y_end[qubit_id], phase_z = phase_z_end[qubit_id])

/var/folders/s4/3cvgkkn17hg628pzrzzjnhww0000gn/T/ipykernel_31068/2374625257.py:4: DeprecationWarning: The QuantumCircuit.__iadd__() method is being deprecated. Use the compose() (potentially with the inplace=True argument) and tensor() methods which are more flexible w.r.t circuit register compatibility.
  circuit += orign_circuit


In [20]:
circuit.draw()

┌───┐        ┌────────────────┐┌────────────┐               »
q_0: ───────┤ X ├────────┤ Ry(6.8272e-06) ├┤ Rz(1.7169) ├───────■───────»
     ┌──────┴───┴──────┐ └─┬────────────┬─┘└────────────┘       │       »
q_1: ┤ Ry(-1.6337e-05) ├───┤ Rz(1.5283) ├───────────────────────■───────»
     └──────┬───┬──────┘┌──┴────────────┴─┐┌────────────┐               »
q_2: ───────┤ X ├───────┤ Ry(-1.9505e-05) ├┤ Rz(1.8468) ├───────────────»
     ┌──────┴───┴──────┐└──┬────────────┬─┘└────────────┘┌─────────────┐»
q_3: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├────────■───────┤ Rz(-1.9184) ├»
     └──────┬───┬──────┘ ┌─┴────────────┴─┐      │       └┬───────────┬┘»
q_4: ───────┤ X ├────────┤ Ry(6.1035e-05) ├──────┼────────┤ Rz(1.818) ├─»
      ┌─────┴───┴──────┐ └─┬───────────┬──┘      │        └───────────┘ »
q_5: ─┤ Ry(5.9653e-06) ├───┤ Rz(1.829) ├─────────┼──────────────────────»
      └─────┬───┬──────┘ ┌─┴───────────┴──┐      │        ┌────────────┐»
q_6: ───────┤ X ├────────┤ Ry(9.3127e-06) ├──────┼────────┤ Rz(1.7187) ├»
      ┌─────┴───┴──────┐ ├────────────────┤      │        └────────────┘»
q_7: ─┤ Ry(-0.0043765) ├─┤ Rz(0.00058093) ├──────┼──────────────────────»
      └─────┬───┬──────┘ └────────────────┘      │                      »
q_8: ───────┤ H ├────────────────────────────────■──────────────────────»
            └───┘                                                       »
«     ┌────────────────┐   ┌────────────┐                                    »
«q_0: ┤ Ry(1.7553e-05) ├───┤ Rz(1.5641) ├────────────────────────────────────»
«     └────────────────┘┌──┴────────────┴─┐┌─────────────┐                   »
«q_1: ────────■─────────┤ Ry(-5.2173e-06) ├┤ Rz(0.89072) ├───────────────────»
«             │         └─────────────────┘└─────────────┘   ┌──────────────┐»
«q_2: ────────■────────────────────────────────────────────■─┤ Ry(2.73e-05) ├»
«     ┌────────────────┐┌─────────────────┐ ┌────────────┐ │ └──────────────┘»
«q_3: ┤ Ry(4.5835e-05) ├┤ Ry(-4.5835e-05) ├─┤ Rz(1.9184) ├─■────────■────────»
«     └────────────────┘└─────────────────┘ └────────────┘          │        »
«q_4: ──────────────────────────────────────────────────────────────■────────»
«                                                                            »
«q_5: ───────────────────────────────────────────────────────────────────────»
«                                                                            »
«q_6: ───────────────────────────────────────────────────────────────────────»
«                                                                            »
«q_7: ───────────────────────────────────────────────────────────────────────»
«                                                                            »
«q_8: ───────────────────────────────────────────────────────────────────────»
«                                                                            »
«                                                            »
«q_0: ───────────────────────────────────────────────────────»
«                                                            »
«q_1: ───────────────────────────────────────────────────────»
«      ┌─────────────┐                                       »
«q_2: ─┤ Rz(0.88955) ├───────────────────────────────────────»
«     ┌┴─────────────┴─┐ ┌──────────────┐   ┌─────────────┐  »
«q_3: ┤ Ry(1.6108e-06) ├─┤ Rz(-0.12592) ├───┤ Rz(0.12592) ├──»
«     └────────────────┘┌┴──────────────┴┐  └┬────────────┤  »
«q_4: ────────■─────────┤ Ry(-8.148e-06) ├───┤ Rz(1.0747) ├──»
«             │         └────────────────┘┌──┴────────────┴─┐»
«q_5: ────────■─────────────────■─────────┤ Ry(-8.6542e-06) ├»
«                               │         └─────────────────┘»
«q_6: ──────────────────────────■──────────────────■─────────»
«                                                  │         »
«q_7: ─────────────────────────────────────────────■─────────»
«                                                            »
«q_8: ────────────────────────────

In [22]:
pauli_list = read_from_file('HF_hamiltonian.txt')
pauli_commute = find_commute_groups(pauli_list)

In [24]:
#generate individual measurment circuits that changes the basis
meas_qcs = []
for i in range(0, len(pauli_commute)):
    temp_qc = MeasureCircuit(pauli_commute[i], num_qubits = 8,num_qargs = 9)
    meas_qcs.append(temp_qc)
    print(temp_qc)

YXXYYXXY
     ┌──────────────┐
q_0: ┤ U(π/2,0,π/2) ├
     └┬────────────┬┘
q_1: ─┤ U(π/2,0,π) ├─
      ├────────────┤ 
q_2: ─┤ U(π/2,0,π) ├─
     ┌┴────────────┴┐
q_3: ┤ U(π/2,0,π/2) ├
     ├──────────────┤
q_4: ┤ U(π/2,0,π/2) ├
     └┬────────────┬┘
q_5: ─┤ U(π/2,0,π) ├─
      ├────────────┤ 
q_6: ─┤ U(π/2,0,π) ├─
     ┌┴────────────┴┐
q_7: ┤ U(π/2,0,π/2) ├
     └──────────────┘
q_8: ────────────────
                     
XXXXYXXY
      ┌────────────┐ 
q_0: ─┤ U(π/2,0,π) ├─
      ├────────────┤ 
q_1: ─┤ U(π/2,0,π) ├─
      ├────────────┤ 
q_2: ─┤ U(π/2,0,π) ├─
      ├────────────┤ 
q_3: ─┤ U(π/2,0,π) ├─
     ┌┴────────────┴┐
q_4: ┤ U(π/2,0,π/2) ├
     └┬────────────┬┘
q_5: ─┤ U(π/2,0,π) ├─
      ├────────────┤ 
q_6: ─┤ U(π/2,0,π) ├─
     ┌┴────────────┴┐
q_7: ┤ U(π/2,0,π/2) ├
     └──────────────┘
q_8: ────────────────
                     
YXXYXXXX
     ┌──────────────┐
q_0: ┤ U(π/2,0,π/2) ├
     └┬────────────┬┘
q_1: ─┤ U(π/2,0,π) ├─
      ├────────────┤ 
q_2: ─┤ U(π/2,0,π) ├─
     

In [25]:
circuit_list = []
for meas in meas_qcs:
    temp_circuit = circuit.copy()
    temp_circuit += meas
    circuit_list.append(temp_circuit)

/var/folders/s4/3cvgkkn17hg628pzrzzjnhww0000gn/T/ipykernel_31068/1717817760.py:4: DeprecationWarning: The QuantumCircuit.__iadd__() method is being deprecated. Use the compose() (potentially with the inplace=True argument) and tensor() methods which are more flexible w.r.t circuit register compatibility.
  temp_circuit += meas


In [26]:
circuit_list[-2].draw()

┌───┐        ┌────────────────┐┌────────────┐               »
q_0: ───────┤ X ├────────┤ Ry(6.8272e-06) ├┤ Rz(1.7169) ├───────■───────»
     ┌──────┴───┴──────┐ └─┬────────────┬─┘└────────────┘       │       »
q_1: ┤ Ry(-1.6337e-05) ├───┤ Rz(1.5283) ├───────────────────────■───────»
     └──────┬───┬──────┘┌──┴────────────┴─┐┌────────────┐               »
q_2: ───────┤ X ├───────┤ Ry(-1.9505e-05) ├┤ Rz(1.8468) ├───────────────»
     ┌──────┴───┴──────┐└──┬────────────┬─┘└────────────┘┌─────────────┐»
q_3: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├────────■───────┤ Rz(-1.9184) ├»
     └──────┬───┬──────┘ ┌─┴────────────┴─┐      │       └┬───────────┬┘»
q_4: ───────┤ X ├────────┤ Ry(6.1035e-05) ├──────┼────────┤ Rz(1.818) ├─»
      ┌─────┴───┴──────┐ └─┬───────────┬──┘      │        └───────────┘ »
q_5: ─┤ Ry(5.9653e-06) ├───┤ Rz(1.829) ├─────────┼──────────────────────»
      └─────┬───┬──────┘ ┌─┴───────────┴──┐      │        ┌────────────┐»
q_6: ───────┤ X ├────────┤ Ry(9.3127e-06) ├──────┼────────┤ Rz(1.7187) ├»
      ┌─────┴───┴──────┐ ├────────────────┤      │        └────────────┘»
q_7: ─┤ Ry(-0.0043765) ├─┤ Rz(0.00058093) ├──────┼──────────────────────»
      └─────┬───┬──────┘ └────────────────┘      │                      »
q_8: ───────┤ H ├────────────────────────────────■──────────────────────»
            └───┘                                                       »
«     ┌────────────────┐   ┌────────────┐                                    »
«q_0: ┤ Ry(1.7553e-05) ├───┤ Rz(1.5641) ├────────────────────────────────────»
«     └────────────────┘┌──┴────────────┴─┐┌─────────────┐                   »
«q_1: ────────■─────────┤ Ry(-5.2173e-06) ├┤ Rz(0.89072) ├───────────────────»
«             │         └─────────────────┘└─────────────┘   ┌──────────────┐»
«q_2: ────────■────────────────────────────────────────────■─┤ Ry(2.73e-05) ├»
«     ┌────────────────┐┌─────────────────┐ ┌────────────┐ │ └──────────────┘»
«q_3: ┤ Ry(4.5835e-05) ├┤ Ry(-4.5835e-05) ├─┤ Rz(1.9184) ├─■────────■────────»
«     └────────────────┘└─────────────────┘ └────────────┘          │        »
«q_4: ──────────────────────────────────────────────────────────────■────────»
«                                                                            »
«q_5: ───────────────────────────────────────────────────────────────────────»
«                                                                            »
«q_6: ───────────────────────────────────────────────────────────────────────»
«                                                                            »
«q_7: ───────────────────────────────────────────────────────────────────────»
«                                                                            »
«q_8: ───────────────────────────────────────────────────────────────────────»
«                                                                            »
«                                                            »
«q_0: ───────────────────────────────────────────────────────»
«                                                            »
«q_1: ───────────────────────────────────────────────────────»
«      ┌─────────────┐                                       »
«q_2: ─┤ Rz(0.88955) ├───────────────────────────────────────»
«     ┌┴─────────────┴─┐ ┌──────────────┐   ┌─────────────┐  »
«q_3: ┤ Ry(1.6108e-06) ├─┤ Rz(-0.12592) ├───┤ Rz(0.12592) ├──»
«     └────────────────┘┌┴──────────────┴┐  └┬────────────┤  »
«q_4: ────────■─────────┤ Ry(-8.148e-06) ├───┤ Rz(1.0747) ├──»
«             │         └────────────────┘┌──┴────────────┴─┐»
«q_5: ────────■─────────────────■─────────┤ Ry(-8.6542e-06) ├»
«                               │         └─────────────────┘»
«q_6: ──────────────────────────■──────────────────■─────────»
«                                                  │         »
«q_7: ─────────────────────────────────────────────■─────────»
«                                                            »
«q_8: ────────────────────────────

In [27]:
# cuts = []
# for i in range(0, 1):
#     if i == 0 or i == qubits - 1:
#         cut = [(circuit.qubits[i], 5),(circuit.qubits[i], 6)]
#     else:
#         cut = [(circuit.qubits[i], 5),(circuit.qubits[i], 4)]
#     cuts += cut

In [28]:
cuts = [(circuit.qubits[3], 5),(circuit.qubits[3], 11)]

In [29]:
fragments_list = []
wire_path_map_list = []
for temp_qc in circuit_list:
    print(temp_qc)
    fragments, wire_path_map = circuit_cutter.cut_circuit(temp_qc, cuts)
    fragments_list.append(fragments)
    wire_path_map_list.append(wire_path_map)

            ┌───┐        ┌────────────────┐┌────────────┐               »
q_0: ───────┤ X ├────────┤ Ry(6.8272e-06) ├┤ Rz(1.7169) ├───────■───────»
     ┌──────┴───┴──────┐ └─┬────────────┬─┘└────────────┘       │       »
q_1: ┤ Ry(-1.6337e-05) ├───┤ Rz(1.5283) ├───────────────────────■───────»
     └──────┬───┬──────┘┌──┴────────────┴─┐┌────────────┐               »
q_2: ───────┤ X ├───────┤ Ry(-1.9505e-05) ├┤ Rz(1.8468) ├───────────────»
     ┌──────┴───┴──────┐└──┬────────────┬─┘└────────────┘┌─────────────┐»
q_3: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├────────■───────┤ Rz(-1.9184) ├»
     └──────┬───┬──────┘ ┌─┴────────────┴─┐      │       └┬───────────┬┘»
q_4: ───────┤ X ├────────┤ Ry(6.1035e-05) ├──────┼────────┤ Rz(1.818) ├─»
      ┌─────┴───┴──────┐ └─┬───────────┬──┘      │        └───────────┘ »
q_5: ─┤ Ry(5.9653e-06) ├───┤ Rz(1.829) ├─────────┼──────────────────────»
      └─────┬───┬──────┘ ┌─┴───────────┴──┐      │        ┌────────────┐»
q_6: ───────┤ X ├────────┤ Ry(9.3127e-

            ┌───┐        ┌────────────────┐┌────────────┐               »
q_0: ───────┤ X ├────────┤ Ry(6.8272e-06) ├┤ Rz(1.7169) ├───────■───────»
     ┌──────┴───┴──────┐ └─┬────────────┬─┘└────────────┘       │       »
q_1: ┤ Ry(-1.6337e-05) ├───┤ Rz(1.5283) ├───────────────────────■───────»
     └──────┬───┬──────┘┌──┴────────────┴─┐┌────────────┐               »
q_2: ───────┤ X ├───────┤ Ry(-1.9505e-05) ├┤ Rz(1.8468) ├───────────────»
     ┌──────┴───┴──────┐└──┬────────────┬─┘└────────────┘┌─────────────┐»
q_3: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├────────■───────┤ Rz(-1.9184) ├»
     └──────┬───┬──────┘ ┌─┴────────────┴─┐      │       └┬───────────┬┘»
q_4: ───────┤ X ├────────┤ Ry(6.1035e-05) ├──────┼────────┤ Rz(1.818) ├─»
      ┌─────┴───┴──────┐ └─┬───────────┬──┘      │        └───────────┘ »
q_5: ─┤ Ry(5.9653e-06) ├───┤ Rz(1.829) ├─────────┼──────────────────────»
      └─────┬───┬──────┘ ┌─┴───────────┴──┐      │        ┌────────────┐»
q_6: ───────┤ X ├────────┤ Ry(9.3127e-

            ┌───┐        ┌────────────────┐┌────────────┐               »
q_0: ───────┤ X ├────────┤ Ry(6.8272e-06) ├┤ Rz(1.7169) ├───────■───────»
     ┌──────┴───┴──────┐ └─┬────────────┬─┘└────────────┘       │       »
q_1: ┤ Ry(-1.6337e-05) ├───┤ Rz(1.5283) ├───────────────────────■───────»
     └──────┬───┬──────┘┌──┴────────────┴─┐┌────────────┐               »
q_2: ───────┤ X ├───────┤ Ry(-1.9505e-05) ├┤ Rz(1.8468) ├───────────────»
     ┌──────┴───┴──────┐└──┬────────────┬─┘└────────────┘┌─────────────┐»
q_3: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├────────■───────┤ Rz(-1.9184) ├»
     └──────┬───┬──────┘ ┌─┴────────────┴─┐      │       └┬───────────┬┘»
q_4: ───────┤ X ├────────┤ Ry(6.1035e-05) ├──────┼────────┤ Rz(1.818) ├─»
      ┌─────┴───┴──────┐ └─┬───────────┬──┘      │        └───────────┘ »
q_5: ─┤ Ry(5.9653e-06) ├───┤ Rz(1.829) ├─────────┼──────────────────────»
      └─────┬───┬──────┘ ┌─┴───────────┴──┐      │        ┌────────────┐»
q_6: ───────┤ X ├────────┤ Ry(9.3127e-

            ┌───┐        ┌────────────────┐┌────────────┐               »
q_0: ───────┤ X ├────────┤ Ry(6.8272e-06) ├┤ Rz(1.7169) ├───────■───────»
     ┌──────┴───┴──────┐ └─┬────────────┬─┘└────────────┘       │       »
q_1: ┤ Ry(-1.6337e-05) ├───┤ Rz(1.5283) ├───────────────────────■───────»
     └──────┬───┬──────┘┌──┴────────────┴─┐┌────────────┐               »
q_2: ───────┤ X ├───────┤ Ry(-1.9505e-05) ├┤ Rz(1.8468) ├───────────────»
     ┌──────┴───┴──────┐└──┬────────────┬─┘└────────────┘┌─────────────┐»
q_3: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├────────■───────┤ Rz(-1.9184) ├»
     └──────┬───┬──────┘ ┌─┴────────────┴─┐      │       └┬───────────┬┘»
q_4: ───────┤ X ├────────┤ Ry(6.1035e-05) ├──────┼────────┤ Rz(1.818) ├─»
      ┌─────┴───┴──────┐ └─┬───────────┬──┘      │        └───────────┘ »
q_5: ─┤ Ry(5.9653e-06) ├───┤ Rz(1.829) ├─────────┼──────────────────────»
      └─────┬───┬──────┘ ┌─┴───────────┴──┐      │        ┌────────────┐»
q_6: ───────┤ X ├────────┤ Ry(9.3127e-

            ┌───┐        ┌────────────────┐┌────────────┐               »
q_0: ───────┤ X ├────────┤ Ry(6.8272e-06) ├┤ Rz(1.7169) ├───────■───────»
     ┌──────┴───┴──────┐ └─┬────────────┬─┘└────────────┘       │       »
q_1: ┤ Ry(-1.6337e-05) ├───┤ Rz(1.5283) ├───────────────────────■───────»
     └──────┬───┬──────┘┌──┴────────────┴─┐┌────────────┐               »
q_2: ───────┤ X ├───────┤ Ry(-1.9505e-05) ├┤ Rz(1.8468) ├───────────────»
     ┌──────┴───┴──────┐└──┬────────────┬─┘└────────────┘┌─────────────┐»
q_3: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├────────■───────┤ Rz(-1.9184) ├»
     └──────┬───┬──────┘ ┌─┴────────────┴─┐      │       └┬───────────┬┘»
q_4: ───────┤ X ├────────┤ Ry(6.1035e-05) ├──────┼────────┤ Rz(1.818) ├─»
      ┌─────┴───┴──────┐ └─┬───────────┬──┘      │        └───────────┘ »
q_5: ─┤ Ry(5.9653e-06) ├───┤ Rz(1.829) ├─────────┼──────────────────────»
      └─────┬───┬──────┘ ┌─┴───────────┴──┐      │        ┌────────────┐»
q_6: ───────┤ X ├────────┤ Ry(9.3127e-

...

            ┌───┐        ┌────────────────┐┌────────────┐               »
q_0: ───────┤ X ├────────┤ Ry(6.8272e-06) ├┤ Rz(1.7169) ├───────■───────»
     ┌──────┴───┴──────┐ └─┬────────────┬─┘└────────────┘       │       »
q_1: ┤ Ry(-1.6337e-05) ├───┤ Rz(1.5283) ├───────────────────────■───────»
     └──────┬───┬──────┘┌──┴────────────┴─┐┌────────────┐               »
q_2: ───────┤ X ├───────┤ Ry(-1.9505e-05) ├┤ Rz(1.8468) ├───────────────»
     ┌──────┴───┴──────┐└──┬────────────┬─┘└────────────┘┌─────────────┐»
q_3: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├────────■───────┤ Rz(-1.9184) ├»
     └──────┬───┬──────┘ ┌─┴────────────┴─┐      │       └┬───────────┬┘»
q_4: ───────┤ X ├────────┤ Ry(6.1035e-05) ├──────┼────────┤ Rz(1.818) ├─»
      ┌─────┴───┴──────┐ └─┬───────────┬──┘      │        └───────────┘ »
q_5: ─┤ Ry(5.9653e-06) ├───┤ Rz(1.829) ├─────────┼──────────────────────»
      └─────┬───┬──────┘ ┌─┴───────────┴──┐      │        ┌────────────┐»
q_6: ───────┤ X ├────────┤ Ry(9.3127e-

            ┌───┐        ┌────────────────┐┌────────────┐               »
q_0: ───────┤ X ├────────┤ Ry(6.8272e-06) ├┤ Rz(1.7169) ├───────■───────»
     ┌──────┴───┴──────┐ └─┬────────────┬─┘└────────────┘       │       »
q_1: ┤ Ry(-1.6337e-05) ├───┤ Rz(1.5283) ├───────────────────────■───────»
     └──────┬───┬──────┘┌──┴────────────┴─┐┌────────────┐               »
q_2: ───────┤ X ├───────┤ Ry(-1.9505e-05) ├┤ Rz(1.8468) ├───────────────»
     ┌──────┴───┴──────┐└──┬────────────┬─┘└────────────┘┌─────────────┐»
q_3: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├────────■───────┤ Rz(-1.9184) ├»
     └──────┬───┬──────┘ ┌─┴────────────┴─┐      │       └┬───────────┬┘»
q_4: ───────┤ X ├────────┤ Ry(6.1035e-05) ├──────┼────────┤ Rz(1.818) ├─»
      ┌─────┴───┴──────┐ └─┬───────────┬──┘      │        └───────────┘ »
q_5: ─┤ Ry(5.9653e-06) ├───┤ Rz(1.829) ├─────────┼──────────────────────»
      └─────┬───┬──────┘ ┌─┴───────────┴──┐      │        ┌────────────┐»
q_6: ───────┤ X ├────────┤ Ry(9.3127e-

            ┌───┐        ┌────────────────┐┌────────────┐               »
q_0: ───────┤ X ├────────┤ Ry(6.8272e-06) ├┤ Rz(1.7169) ├───────■───────»
     ┌──────┴───┴──────┐ └─┬────────────┬─┘└────────────┘       │       »
q_1: ┤ Ry(-1.6337e-05) ├───┤ Rz(1.5283) ├───────────────────────■───────»
     └──────┬───┬──────┘┌──┴────────────┴─┐┌────────────┐               »
q_2: ───────┤ X ├───────┤ Ry(-1.9505e-05) ├┤ Rz(1.8468) ├───────────────»
     ┌──────┴───┴──────┐└──┬────────────┬─┘└────────────┘┌─────────────┐»
q_3: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├────────■───────┤ Rz(-1.9184) ├»
     └──────┬───┬──────┘ ┌─┴────────────┴─┐      │       └┬───────────┬┘»
q_4: ───────┤ X ├────────┤ Ry(6.1035e-05) ├──────┼────────┤ Rz(1.818) ├─»
      ┌─────┴───┴──────┐ └─┬───────────┬──┘      │        └───────────┘ »
q_5: ─┤ Ry(5.9653e-06) ├───┤ Rz(1.829) ├─────────┼──────────────────────»
      └─────┬───┬──────┘ ┌─┴───────────┴──┐      │        ┌────────────┐»
q_6: ───────┤ X ├────────┤ Ry(9.3127e-

            ┌───┐        ┌────────────────┐┌────────────┐               »
q_0: ───────┤ X ├────────┤ Ry(6.8272e-06) ├┤ Rz(1.7169) ├───────■───────»
     ┌──────┴───┴──────┐ └─┬────────────┬─┘└────────────┘       │       »
q_1: ┤ Ry(-1.6337e-05) ├───┤ Rz(1.5283) ├───────────────────────■───────»
     └──────┬───┬──────┘┌──┴────────────┴─┐┌────────────┐               »
q_2: ───────┤ X ├───────┤ Ry(-1.9505e-05) ├┤ Rz(1.8468) ├───────────────»
     ┌──────┴───┴──────┐└──┬────────────┬─┘└────────────┘┌─────────────┐»
q_3: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├────────■───────┤ Rz(-1.9184) ├»
     └──────┬───┬──────┘ ┌─┴────────────┴─┐      │       └┬───────────┬┘»
q_4: ───────┤ X ├────────┤ Ry(6.1035e-05) ├──────┼────────┤ Rz(1.818) ├─»
      ┌─────┴───┴──────┐ └─┬───────────┬──┘      │        └───────────┘ »
q_5: ─┤ Ry(5.9653e-06) ├───┤ Rz(1.829) ├─────────┼──────────────────────»
      └─────┬───┬──────┘ ┌─┴───────────┴──┐      │        ┌────────────┐»
q_6: ───────┤ X ├────────┤ Ry(9.3127e-

            ┌───┐        ┌────────────────┐┌────────────┐               »
q_0: ───────┤ X ├────────┤ Ry(6.8272e-06) ├┤ Rz(1.7169) ├───────■───────»
     ┌──────┴───┴──────┐ └─┬────────────┬─┘└────────────┘       │       »
q_1: ┤ Ry(-1.6337e-05) ├───┤ Rz(1.5283) ├───────────────────────■───────»
     └──────┬───┬──────┘┌──┴────────────┴─┐┌────────────┐               »
q_2: ───────┤ X ├───────┤ Ry(-1.9505e-05) ├┤ Rz(1.8468) ├───────────────»
     ┌──────┴───┴──────┐└──┬────────────┬─┘└────────────┘┌─────────────┐»
q_3: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├────────■───────┤ Rz(-1.9184) ├»
     └──────┬───┬──────┘ ┌─┴────────────┴─┐      │       └┬───────────┬┘»
q_4: ───────┤ X ├────────┤ Ry(6.1035e-05) ├──────┼────────┤ Rz(1.818) ├─»
      ┌─────┴───┴──────┐ └─┬───────────┬──┘      │        └───────────┘ »
q_5: ─┤ Ry(5.9653e-06) ├───┤ Rz(1.829) ├─────────┼──────────────────────»
      └─────┬───┬──────┘ ┌─┴───────────┴──┐      │        ┌────────────┐»
q_6: ───────┤ X ├────────┤ Ry(9.3127e-

In [30]:
print(wire_path_map_list[0])

{Qubit(QuantumRegister(9, 'q'), 0): ((0, Qubit(QuantumRegister(8, 'q'), 3)),), Qubit(QuantumRegister(9, 'q'), 1): ((0, Qubit(QuantumRegister(8, 'q'), 1)),), Qubit(QuantumRegister(9, 'q'), 2): ((0, Qubit(QuantumRegister(8, 'q'), 6)),), Qubit(QuantumRegister(9, 'q'), 3): ((1, Qubit(QuantumRegister(3, 'q'), 1)), (0, Qubit(QuantumRegister(8, 'q'), 5)), (1, Qubit(QuantumRegister(3, 'q'), 2))), Qubit(QuantumRegister(9, 'q'), 4): ((0, Qubit(QuantumRegister(8, 'q'), 0)),), Qubit(QuantumRegister(9, 'q'), 5): ((0, Qubit(QuantumRegister(8, 'q'), 7)),), Qubit(QuantumRegister(9, 'q'), 6): ((0, Qubit(QuantumRegister(8, 'q'), 4)),), Qubit(QuantumRegister(9, 'q'), 7): ((0, Qubit(QuantumRegister(8, 'q'), 2)),), Qubit(QuantumRegister(9, 'q'), 8): ((1, Qubit(QuantumRegister(3, 'q'), 0)),)}


In [31]:
total_variants = ml.fragment_variants(wire_path_map_list[0])

In [32]:
total_variants

24

In [33]:
shots = 10000 * total_variants

In [34]:
fragments_list[0][0].draw()

┌───┐        ┌────────────────┐┌───────────┐                      »
q_0: ───────┤ X ├────────┤ Ry(6.1035e-05) ├┤ Rz(1.818) ├──────────────────────»
     ┌──────┴───┴──────┐ └─┬────────────┬─┘└───────────┘                      »
q_1: ┤ Ry(-1.6337e-05) ├───┤ Rz(1.5283) ├─────────────────■───────────────────»
     └┬────────────────┤ ┌─┴────────────┴─┐               │                   »
q_2: ─┤ Ry(-0.0043765) ├─┤ Rz(0.00058093) ├───────────────┼───────────────────»
      └─────┬───┬──────┘ ├────────────────┤┌────────────┐ │ ┌────────────────┐»
q_3: ───────┤ X ├────────┤ Ry(6.8272e-06) ├┤ Rz(1.7169) ├─■─┤ Ry(1.7553e-05) ├»
            ├───┤        ├────────────────┤├────────────┤   └────────────────┘»
q_4: ───────┤ X ├────────┤ Ry(9.3127e-06) ├┤ Rz(1.7187) ├─────────────────────»
     ┌──────┴───┴──────┐ └─┬────────────┬─┘└────────────┘                     »
q_5: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├─────────────────────────────────────»
     └──────┬───┬──────┘┌──┴────────────┴─┐┌────────────┐                     »
q_6: ───────┤ X ├───────┤ Ry(-1.9505e-05) ├┤ Rz(1.8468) ├─────────────────────»
      ┌─────┴───┴──────┐└──┬───────────┬──┘└────────────┘                     »
q_7: ─┤ Ry(5.9653e-06) ├───┤ Rz(1.829) ├──────────────────────────────────────»
      └────────────────┘   └───────────┘                                      »
«                                                                            »
«q_0: ─────────────────────────────────────────────■─────────────────────────»
«        ┌─────────────────┐┌─────────────┐        │         ┌────────────┐  »
«q_1: ─■─┤ Ry(-5.2173e-06) ├┤ Rz(0.89072) ├────────┼─────────┤ U(π/2,0,π) ├──»
«      │ └─────────────────┘└─────────────┘        │         └────────────┘  »
«q_2: ─┼───────────────────────────────────────────┼─────────────────────────»
«      │    ┌────────────┐  ┌──────────────┐       │                         »
«q_3: ─┼────┤ Rz(1.5641) ├──┤ U(π/2,0,π/2) ├───────┼─────────────────────────»
«      │    └────────────┘  └──────────────┘       │                         »
«q_4: ─┼───────────────────────────────────────────┼─────────────────────────»
«      │                                           │       ┌────────────────┐»
«q_5: ─┼──────────■────────────────────────────────■───────┤ Ry(1.6108e-06) ├»
«      │          │         ┌──────────────┐┌─────────────┐└─┬────────────┬─┘»
«q_6: ─■──────────■─────────┤ Ry(2.73e-05) ├┤ Rz(0.88955) ├──┤ U(π/2,0,π) ├──»
«                           └──────────────┘└─────────────┘  └────────────┘  »
«q_7: ───────────────────────────────────────────────────────────────────────»
«                                                                            »
«        ┌────────────────┐┌────────────┐  ┌──────────────┐                    »
«q_0: ─■─┤ Ry(-8.148e-06) ├┤ Rz(1.0747) ├──┤ U(π/2,0,π/2) ├────────────────────»
«      │ └────────────────┘└────────────┘  └──────────────┘                    »
«q_1: ─┼───────────────────────────────────────────────────────────────────────»
«      │                                                     ┌────────────────┐»
«q_2: ─┼──────────────────────────────────────────■──────────┤ Ry(-0.0044055) ├»
«      │                                          │          └────────────────┘»
«q_3: ─┼──────────────────────────────────────────┼────────────────────────────»
«      │                                          │         ┌─────────────────┐»
«q_4: ─┼─────────────────────────■────────────────■─────────┤ Ry(-8.1451e-06) ├»
«      │  ┌──────────────┐       │                          └─────────────────┘»
«q_5: ─┼──┤ Rz(-0.12592) ├───────┼─────────────────────────────────────────────»
«      │  └──────────────┘       │                                             »
«q_6: ─┼─────────────────────────┼─────────────────────────────────────────────»
«      │                         │       ┌─────────────────┐  ┌──────────────┐ »
«q_7: ─■─────────────────────────■───────┤ Ry(-8.6542e-06) ├──┤ Rz(-0.21554) ├─»
«            

In [35]:
fragment_cuts_list = []
for index in range(0, len(fragments_list)):
    for idx, fragment in enumerate(fragments_list[index]):
        print(f"fragment {idx}:")
        print(fragment)
        print()
    fragment_cuts = ml.fragment_cuts(wire_path_map_list[index])
    fragment_cuts_list.append(fragment_cuts)


fragment 0:
            ┌───┐        ┌────────────────┐┌───────────┐                      »
q_0: ───────┤ X ├────────┤ Ry(6.1035e-05) ├┤ Rz(1.818) ├──────────────────────»
     ┌──────┴───┴──────┐ └─┬────────────┬─┘└───────────┘                      »
q_1: ┤ Ry(-1.6337e-05) ├───┤ Rz(1.5283) ├─────────────────■───────────────────»
     └┬────────────────┤ ┌─┴────────────┴─┐               │                   »
q_2: ─┤ Ry(-0.0043765) ├─┤ Rz(0.00058093) ├───────────────┼───────────────────»
      └─────┬───┬──────┘ ├────────────────┤┌────────────┐ │ ┌────────────────┐»
q_3: ───────┤ X ├────────┤ Ry(6.8272e-06) ├┤ Rz(1.7169) ├─■─┤ Ry(1.7553e-05) ├»
            ├───┤        ├────────────────┤├────────────┤   └────────────────┘»
q_4: ───────┤ X ├────────┤ Ry(9.3127e-06) ├┤ Rz(1.7187) ├─────────────────────»
     ┌──────┴───┴──────┐ └─┬────────────┬─┘└────────────┘                     »
q_5: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├─────────────────────────────────────»
     └──────┬───┬──────┘┌──┴

            ┌───┐        ┌────────────────┐┌───────────┐                      »
q_0: ───────┤ X ├────────┤ Ry(6.1035e-05) ├┤ Rz(1.818) ├──────────────────────»
     ┌──────┴───┴──────┐ └─┬────────────┬─┘└───────────┘                      »
q_1: ┤ Ry(-1.6337e-05) ├───┤ Rz(1.5283) ├─────────────────■───────────────────»
     └┬────────────────┤ ┌─┴────────────┴─┐               │                   »
q_2: ─┤ Ry(-0.0043765) ├─┤ Rz(0.00058093) ├───────────────┼───────────────────»
      └─────┬───┬──────┘ ├────────────────┤┌────────────┐ │ ┌────────────────┐»
q_3: ───────┤ X ├────────┤ Ry(6.8272e-06) ├┤ Rz(1.7169) ├─■─┤ Ry(1.7553e-05) ├»
            ├───┤        ├────────────────┤├────────────┤   └────────────────┘»
q_4: ───────┤ X ├────────┤ Ry(9.3127e-06) ├┤ Rz(1.7187) ├─────────────────────»
     ┌──────┴───┴──────┐ └─┬────────────┬─┘└────────────┘                     »
q_5: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├─────────────────────────────────────»
     └──────┬───┬──────┘┌──┴────────────

            ┌───┐        ┌────────────────┐┌───────────┐                      »
q_0: ───────┤ X ├────────┤ Ry(6.1035e-05) ├┤ Rz(1.818) ├──────────────────────»
     ┌──────┴───┴──────┐ └─┬────────────┬─┘└───────────┘                      »
q_1: ┤ Ry(-1.6337e-05) ├───┤ Rz(1.5283) ├─────────────────■───────────────────»
     └┬────────────────┤ ┌─┴────────────┴─┐               │                   »
q_2: ─┤ Ry(-0.0043765) ├─┤ Rz(0.00058093) ├───────────────┼───────────────────»
      └─────┬───┬──────┘ ├────────────────┤┌────────────┐ │ ┌────────────────┐»
q_3: ───────┤ X ├────────┤ Ry(6.8272e-06) ├┤ Rz(1.7169) ├─■─┤ Ry(1.7553e-05) ├»
            ├───┤        ├────────────────┤├────────────┤   └────────────────┘»
q_4: ───────┤ X ├────────┤ Ry(9.3127e-06) ├┤ Rz(1.7187) ├─────────────────────»
     ┌──────┴───┴──────┐ └─┬────────────┬─┘└────────────┘                     »
q_5: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├─────────────────────────────────────»
     └──────┬───┬──────┘┌──┴────────────

            ┌───┐        ┌────────────────┐┌───────────┐                      »
q_0: ───────┤ X ├────────┤ Ry(6.1035e-05) ├┤ Rz(1.818) ├──────────────────────»
     ┌──────┴───┴──────┐ └─┬────────────┬─┘└───────────┘                      »
q_1: ┤ Ry(-1.6337e-05) ├───┤ Rz(1.5283) ├─────────────────■───────────────────»
     └┬────────────────┤ ┌─┴────────────┴─┐               │                   »
q_2: ─┤ Ry(-0.0043765) ├─┤ Rz(0.00058093) ├───────────────┼───────────────────»
      └─────┬───┬──────┘ ├────────────────┤┌────────────┐ │ ┌────────────────┐»
q_3: ───────┤ X ├────────┤ Ry(6.8272e-06) ├┤ Rz(1.7169) ├─■─┤ Ry(1.7553e-05) ├»
            ├───┤        ├────────────────┤├────────────┤   └────────────────┘»
q_4: ───────┤ X ├────────┤ Ry(9.3127e-06) ├┤ Rz(1.7187) ├─────────────────────»
     ┌──────┴───┴──────┐ └─┬────────────┬─┘└────────────┘                     »
q_5: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├─────────────────────────────────────»
     └──────┬───┬──────┘┌──┴────────────

            ┌───┐        ┌────────────────┐┌───────────┐                      »
q_0: ───────┤ X ├────────┤ Ry(6.1035e-05) ├┤ Rz(1.818) ├──────────────────────»
     ┌──────┴───┴──────┐ └─┬────────────┬─┘└───────────┘                      »
q_1: ┤ Ry(-1.6337e-05) ├───┤ Rz(1.5283) ├─────────────────■───────────────────»
     └┬────────────────┤ ┌─┴────────────┴─┐               │                   »
q_2: ─┤ Ry(-0.0043765) ├─┤ Rz(0.00058093) ├───────────────┼───────────────────»
      └─────┬───┬──────┘ ├────────────────┤┌────────────┐ │ ┌────────────────┐»
q_3: ───────┤ X ├────────┤ Ry(6.8272e-06) ├┤ Rz(1.7169) ├─■─┤ Ry(1.7553e-05) ├»
            ├───┤        ├────────────────┤├────────────┤   └────────────────┘»
q_4: ───────┤ X ├────────┤ Ry(9.3127e-06) ├┤ Rz(1.7187) ├─────────────────────»
     ┌──────┴───┴──────┐ └─┬────────────┬─┘└────────────┘                     »
q_5: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├─────────────────────────────────────»
     └──────┬───┬──────┘┌──┴────────────

...

            ┌───┐        ┌────────────────┐┌───────────┐                      »
q_0: ───────┤ X ├────────┤ Ry(6.1035e-05) ├┤ Rz(1.818) ├──────────────────────»
     ┌──────┴───┴──────┐ └─┬────────────┬─┘└───────────┘                      »
q_1: ┤ Ry(-1.6337e-05) ├───┤ Rz(1.5283) ├─────────────────■───────────────────»
     └┬────────────────┤ ┌─┴────────────┴─┐               │                   »
q_2: ─┤ Ry(-0.0043765) ├─┤ Rz(0.00058093) ├───────────────┼───────────────────»
      └─────┬───┬──────┘ ├────────────────┤┌────────────┐ │ ┌────────────────┐»
q_3: ───────┤ X ├────────┤ Ry(6.8272e-06) ├┤ Rz(1.7169) ├─■─┤ Ry(1.7553e-05) ├»
            ├───┤        ├────────────────┤├────────────┤   └────────────────┘»
q_4: ───────┤ X ├────────┤ Ry(9.3127e-06) ├┤ Rz(1.7187) ├─────────────────────»
     ┌──────┴───┴──────┐ └─┬────────────┬─┘└────────────┘                     »
q_5: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├─────────────────────────────────────»
     └──────┬───┬──────┘┌──┴────────────

            ┌───┐        ┌────────────────┐┌───────────┐                      »
q_0: ───────┤ X ├────────┤ Ry(6.1035e-05) ├┤ Rz(1.818) ├──────────────────────»
     ┌──────┴───┴──────┐ └─┬────────────┬─┘└───────────┘                      »
q_1: ┤ Ry(-1.6337e-05) ├───┤ Rz(1.5283) ├─────────────────■───────────────────»
     └┬────────────────┤ ┌─┴────────────┴─┐               │                   »
q_2: ─┤ Ry(-0.0043765) ├─┤ Rz(0.00058093) ├───────────────┼───────────────────»
      └─────┬───┬──────┘ ├────────────────┤┌────────────┐ │ ┌────────────────┐»
q_3: ───────┤ X ├────────┤ Ry(6.8272e-06) ├┤ Rz(1.7169) ├─■─┤ Ry(1.7553e-05) ├»
            ├───┤        ├────────────────┤├────────────┤   └────────────────┘»
q_4: ───────┤ X ├────────┤ Ry(9.3127e-06) ├┤ Rz(1.7187) ├─────────────────────»
     ┌──────┴───┴──────┐ └─┬────────────┬─┘└────────────┘                     »
q_5: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├─────────────────────────────────────»
     └──────┬───┬──────┘┌──┴────────────

            ┌───┐        ┌────────────────┐┌───────────┐                      »
q_0: ───────┤ X ├────────┤ Ry(6.1035e-05) ├┤ Rz(1.818) ├──────────────────────»
     ┌──────┴───┴──────┐ └─┬────────────┬─┘└───────────┘                      »
q_1: ┤ Ry(-1.6337e-05) ├───┤ Rz(1.5283) ├─────────────────■───────────────────»
     └┬────────────────┤ ┌─┴────────────┴─┐               │                   »
q_2: ─┤ Ry(-0.0043765) ├─┤ Rz(0.00058093) ├───────────────┼───────────────────»
      └─────┬───┬──────┘ ├────────────────┤┌────────────┐ │ ┌────────────────┐»
q_3: ───────┤ X ├────────┤ Ry(6.8272e-06) ├┤ Rz(1.7169) ├─■─┤ Ry(1.7553e-05) ├»
            ├───┤        ├────────────────┤├────────────┤   └────────────────┘»
q_4: ───────┤ X ├────────┤ Ry(9.3127e-06) ├┤ Rz(1.7187) ├─────────────────────»
     ┌──────┴───┴──────┐ └─┬────────────┬─┘└────────────┘                     »
q_5: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├─────────────────────────────────────»
     └──────┬───┬──────┘┌──┴────────────

            ┌───┐        ┌────────────────┐┌───────────┐                      »
q_0: ───────┤ X ├────────┤ Ry(6.1035e-05) ├┤ Rz(1.818) ├──────────────────────»
     ┌──────┴───┴──────┐ └─┬────────────┬─┘└───────────┘                      »
q_1: ┤ Ry(-1.6337e-05) ├───┤ Rz(1.5283) ├─────────────────■───────────────────»
     └┬────────────────┤ ┌─┴────────────┴─┐               │                   »
q_2: ─┤ Ry(-0.0043765) ├─┤ Rz(0.00058093) ├───────────────┼───────────────────»
      └─────┬───┬──────┘ ├────────────────┤┌────────────┐ │ ┌────────────────┐»
q_3: ───────┤ X ├────────┤ Ry(6.8272e-06) ├┤ Rz(1.7169) ├─■─┤ Ry(1.7553e-05) ├»
            ├───┤        ├────────────────┤├────────────┤   └────────────────┘»
q_4: ───────┤ X ├────────┤ Ry(9.3127e-06) ├┤ Rz(1.7187) ├─────────────────────»
     ┌──────┴───┴──────┐ └─┬────────────┬─┘└────────────┘                     »
q_5: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├─────────────────────────────────────»
     └──────┬───┬──────┘┌──┴────────────

            ┌───┐        ┌────────────────┐┌───────────┐                      »
q_0: ───────┤ X ├────────┤ Ry(6.1035e-05) ├┤ Rz(1.818) ├──────────────────────»
     ┌──────┴───┴──────┐ └─┬────────────┬─┘└───────────┘                      »
q_1: ┤ Ry(-1.6337e-05) ├───┤ Rz(1.5283) ├─────────────────■───────────────────»
     └┬────────────────┤ ┌─┴────────────┴─┐               │                   »
q_2: ─┤ Ry(-0.0043765) ├─┤ Rz(0.00058093) ├───────────────┼───────────────────»
      └─────┬───┬──────┘ ├────────────────┤┌────────────┐ │ ┌────────────────┐»
q_3: ───────┤ X ├────────┤ Ry(6.8272e-06) ├┤ Rz(1.7169) ├─■─┤ Ry(1.7553e-05) ├»
            ├───┤        ├────────────────┤├────────────┤   └────────────────┘»
q_4: ───────┤ X ├────────┤ Ry(9.3127e-06) ├┤ Rz(1.7187) ├─────────────────────»
     ┌──────┴───┴──────┐ └─┬────────────┬─┘└────────────┘                     »
q_5: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├─────────────────────────────────────»
     └──────┬───┬──────┘┌──┴────────────

In [36]:
print(fragment_cuts_list[-1])

[{'prep': 1, 'meas': 1}, {'prep': 1, 'meas': 1}]


In [37]:
wire_path_map

{Qubit(QuantumRegister(9, 'q'), 0): ((0, Qubit(QuantumRegister(8, 'q'), 3)),),
 Qubit(QuantumRegister(9, 'q'), 1): ((0, Qubit(QuantumRegister(8, 'q'), 1)),),
 Qubit(QuantumRegister(9, 'q'), 2): ((0, Qubit(QuantumRegister(8, 'q'), 6)),),
 Qubit(QuantumRegister(9, 'q'), 3): ((1, Qubit(QuantumRegister(3, 'q'), 1)),
  (0, Qubit(QuantumRegister(8, 'q'), 5)),
  (1, Qubit(QuantumRegister(3, 'q'), 2))),
 Qubit(QuantumRegister(9, 'q'), 4): ((0, Qubit(QuantumRegister(8, 'q'), 0)),),
 Qubit(QuantumRegister(9, 'q'), 5): ((0, Qubit(QuantumRegister(8, 'q'), 7)),),
 Qubit(QuantumRegister(9, 'q'), 6): ((0, Qubit(QuantumRegister(8, 'q'), 4)),),
 Qubit(QuantumRegister(9, 'q'), 7): ((0, Qubit(QuantumRegister(8, 'q'), 2)),),
 Qubit(QuantumRegister(9, 'q'), 8): ((1, Qubit(QuantumRegister(3, 'q'), 0)),)}

In [38]:
num_fragments = len(fragments)
num_fragments

2

In [39]:
num_tomo_circuits = len(meas_qcs)
num_tomo_circuits

76

In [40]:
fragments[0].draw()

┌───┐        ┌────────────────┐┌───────────┐                      »
q_0: ───────┤ X ├────────┤ Ry(6.1035e-05) ├┤ Rz(1.818) ├──────────────────────»
     ┌──────┴───┴──────┐ └─┬────────────┬─┘└───────────┘                      »
q_1: ┤ Ry(-1.6337e-05) ├───┤ Rz(1.5283) ├─────────────────■───────────────────»
     └┬────────────────┤ ┌─┴────────────┴─┐               │                   »
q_2: ─┤ Ry(-0.0043765) ├─┤ Rz(0.00058093) ├───────────────┼───────────────────»
      └─────┬───┬──────┘ ├────────────────┤┌────────────┐ │ ┌────────────────┐»
q_3: ───────┤ X ├────────┤ Ry(6.8272e-06) ├┤ Rz(1.7169) ├─■─┤ Ry(1.7553e-05) ├»
            ├───┤        ├────────────────┤├────────────┤   └────────────────┘»
q_4: ───────┤ X ├────────┤ Ry(9.3127e-06) ├┤ Rz(1.7187) ├─────────────────────»
     ┌──────┴───┴──────┐ └─┬────────────┬─┘└────────────┘                     »
q_5: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├─────────────────────────────────────»
     └──────┬───┬──────┘┌──┴────────────┴─┐┌────────────┐                     »
q_6: ───────┤ X ├───────┤ Ry(-1.9505e-05) ├┤ Rz(1.8468) ├─────────────────────»
      ┌─────┴───┴──────┐└──┬───────────┬──┘└────────────┘                     »
q_7: ─┤ Ry(5.9653e-06) ├───┤ Rz(1.829) ├──────────────────────────────────────»
      └────────────────┘   └───────────┘                                      »
«                                                                            »
«q_0: ─────────────────────────────────────────────■─────────────────────────»
«        ┌─────────────────┐┌─────────────┐        │                         »
«q_1: ─■─┤ Ry(-5.2173e-06) ├┤ Rz(0.89072) ├────────┼─────────────────────────»
«      │ └─────────────────┘└─────────────┘        │                         »
«q_2: ─┼───────────────────────────────────────────┼─────────────────────────»
«      │    ┌────────────┐   ┌────────────┐        │                         »
«q_3: ─┼────┤ Rz(1.5641) ├───┤ U(π/2,0,π) ├────────┼─────────────────────────»
«      │    └────────────┘   └────────────┘        │                         »
«q_4: ─┼───────────────────────────────────────────┼─────────────────────────»
«      │                                           │       ┌────────────────┐»
«q_5: ─┼──────────■────────────────────────────────■───────┤ Ry(1.6108e-06) ├»
«      │          │         ┌──────────────┐┌─────────────┐└────────────────┘»
«q_6: ─■──────────■─────────┤ Ry(2.73e-05) ├┤ Rz(0.88955) ├──────────────────»
«                           └──────────────┘└─────────────┘                  »
«q_7: ───────────────────────────────────────────────────────────────────────»
«                                                                            »
«        ┌────────────────┐┌────────────┐                                      »
«q_0: ─■─┤ Ry(-8.148e-06) ├┤ Rz(1.0747) ├──────────────────────────────────────»
«      │ └────────────────┘└────────────┘                                      »
«q_1: ─┼───────────────────────────────────────────────────────────────────────»
«      │                                                     ┌────────────────┐»
«q_2: ─┼──────────────────────────────────────────■──────────┤ Ry(-0.0044055) ├»
«      │                                          │          └────────────────┘»
«q_3: ─┼──────────────────────────────────────────┼────────────────────────────»
«      │                                          │         ┌─────────────────┐»
«q_4: ─┼─────────────────────────■────────────────■─────────┤ Ry(-8.1451e-06) ├»
«      │  ┌──────────────┐       │                          └─────────────────┘»
«q_5: ─┼──┤ Rz(-0.12592) ├───────┼─────────────────────────────────────────────»
«      │  └──────────────┘       │                                             »
«q_6: ─┼─────────────────────────┼─────────────────────────────────────────────»
«      │                         │       ┌─────────────────┐  ┌──────────────┐ »
«q_7: ─■─────────────────────────■───────┤ Ry(-8.6542e-06) ├──┤ Rz(-0.21554) ├─»
«            

In [41]:
fragments[1].draw()

┌───┐                                               »
q_0: ───────┤ H ├───────────────────────────■─────────────────■─»
     ┌──────┴───┴──────┐   ┌────────────┐   │ ┌─────────────┐ │ »
q_1: ┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├───■─┤ Rz(-1.9184) ├─┼─»
     └─┬─────────────┬─┘┌──┴────────────┴─┐   └─────────────┘ │ »
q_2: ──┤ Rz(0.12592) ├──┤ Ry(-1.6108e-06) ├───────────────────■─»
       └─────────────┘  └─────────────────┘                     »
«           ┌───┐                       
«q_0: ──────┤ H ├───────────────────────
«     ┌─────┴───┴──────┐                
«q_1: ┤ Ry(4.5835e-05) ├────────────────
«     ├────────────────┤┌──────────────┐
«q_2: ┤ Ry(1.6108e-06) ├┤ Rz(-0.12592) ├
«     └────────────────┘└──────────────┘

In [42]:
hardware_index = 0

In [43]:
print(shots)

240000


In [44]:
tomography_circuits = []
for idx in range(0, len(fragments_list)):
    fragments = fragments_list[idx]
    wire_path_map = wire_path_map_list[idx]
    temp_frag_circuits = [0] * len(fragments)
    for i in range(0, len(fragments)):
        if i == hardware_index:
            temp_frag_circuits[i] = collect_fragment_circuits(fragments[i], i, wire_path_map,
                                         shots = shots // total_variants,
                                         tomography_backend = simulation_backend)
        else:
            temp_frag_circuits[i] = collect_fragment_circuits(fragments[i], i, wire_path_map,
                                         shots = shots // total_variants,
                                         tomography_backend = simulation_backend)
    tomography_circuits.append(temp_frag_circuits)

In [45]:
#contains 34 basis
len(tomography_circuits)

76

In [46]:
#contains two fragments
len(tomography_circuits[0])

2

In [47]:
len(tomography_circuits[0][1])

1

In [48]:
#tomography circuits
len(tomography_circuits[0][1][0])

12

In [49]:
multi_exp_circuits = [[],[]]
for i in range(0, len(tomography_circuits)):
    #for each basis collect the three fragments:
    for j in range(0, num_fragments):
        fragment_circ = tomography_circuits[i][j][0]
        multi_exp_circuits[j] += fragment_circ

In [51]:
#[9,8,11,14,13,12,10,7]
#31650742
#[13,8,7,9,10,14,11,12]

In [50]:
multi_exp_circuits[hardware_index][-200].draw()

░        ┌───┐        ┌────────────────┐»
   q_0: ────────────────────░────────┤ X ├────────┤ Ry(6.1035e-05) ├»
                            ░ ┌──────┴───┴──────┐ └─┬────────────┬─┘»
   q_1: ────────────────────░─┤ Ry(-1.6337e-05) ├───┤ Rz(1.5283) ├──»
                            ░ └┬────────────────┤ ┌─┴────────────┴─┐»
   q_2: ────────────────────░──┤ Ry(-0.0043765) ├─┤ Rz(0.00058093) ├»
                            ░  └─────┬───┬──────┘ ├────────────────┤»
   q_3: ────────────────────░────────┤ X ├────────┤ Ry(6.8272e-06) ├»
                            ░        ├───┤        ├────────────────┤»
   q_4: ────────────────────░────────┤ X ├────────┤ Ry(9.3127e-06) ├»
        ┌─────────────────┐ ░ ┌──────┴───┴──────┐ └─┬────────────┬─┘»
   q_5: ┤ U3(-1.9106,π,0) ├─░─┤ Ry(-4.5835e-05) ├───┤ Rz(1.9184) ├──»
        └─────────────────┘ ░ └──────┬───┬──────┘┌──┴────────────┴─┐»
   q_6: ────────────────────░────────┤ X ├───────┤ Ry(-1.9505e-05) ├»
                            ░  ┌─────┴───┴──────┐└──┬───────────┬──┘»
   q_7: ────────────────────░──┤ Ry(5.9653e-06) ├───┤ Rz(1.829) ├───»
                            ░  └────────────────┘   └───────────┘   »
c118_0: ════════════════════════════════════════════════════════════»
                                                                    »
c118_1: ════════════════════════════════════════════════════════════»
                                                                    »
c118_2: ════════════════════════════════════════════════════════════»
                                                                    »
c118_3: ════════════════════════════════════════════════════════════»
                                                                    »
c118_4: ════════════════════════════════════════════════════════════»
                                                                    »
c118_5: ════════════════════════════════════════════════════════════»
                                                                    »
c118_6: ════════════════════════════════════════════════════════════»
                                                                    »
c118_7: ════════════════════════════════════════════════════════════»
                                                                    »
«        ┌───────────┐                                            »
«   q_0: ┤ Rz(1.818) ├────────────────────────────────────────────»
«        └───────────┘                         ┌─────────────────┐»
«   q_1: ───────────────■────────────────────■─┤ Ry(-5.2173e-06) ├»
«                       │                    │ └─────────────────┘»
«   q_2: ───────────────┼────────────────────┼────────────────────»
«        ┌────────────┐ │ ┌────────────────┐ │    ┌────────────┐  »
«   q_3: ┤ Rz(1.7169) ├─■─┤ Ry(1.7553e-05) ├─┼────┤ Rz(1.5641) ├──»
«        ├────────────┤   └────────────────┘ │    └────────────┘  »
«   q_4: ┤ Rz(1.7187) ├──────────────────────┼────────────────────»
«        └────────────┘                      │                    »
«   q_5: ────────────────────────────────────┼──────────■─────────»
«        ┌────────────┐                      │          │         »
«   q_6: ┤ Rz(1.8468) ├──────────────────────■──────────■─────────»
«        └────────────┘                                           »
«   q_7: ─────────────────────────────────────────────────────────»
«                                                                 »
«c118_0: ═════════════════════════════════════════════════════════»
«                                                                 »
«c118_1: ═════════════════════════════════════════════════════════»
«                                                                 »
«c118_2: ═════════════════════════════════════════════════════════»
«                                                                 »
«c118_3: ═════════════════════════════════════════════════════════»
«                                                                 »
«c118_4: ═════════

In [61]:
len(multi_exp_circuits[0])

408

In [68]:
frag_datas = [0] * num_fragments
for i in range(0, num_fragments):
    if i == hardware_index:
        frag_datas[i] = run_circuits(multi_exp_circuits[i], initial_layout = [13,8,7,9,10,14,11,12],
                                     backend = device, shots = shots // total_variants, 
                                     optimization_level = 3, monitor_jobs = True)
    else:
        frag_datas[i] = run_circuits(multi_exp_circuits[i], initial_layout = None,
                                     backend = simulation_backend, shots = shots // total_variants,
                                     optimization_level = 3, monitor_jobs = True, noise_model = None)
       

jobset_id:  522263dd7d0b471fad3ed98af069471a-1670516315364028
job_id:  2fcd1c04-c1d3-4024-b60d-e4f96df50526
Job Status: job has successfully run


In [69]:
frag_datas[1]

[Result(backend_name='qasm_simulator', backend_version='0.11.1', qobj_id='ae3299a1-518d-4de9-8811-6c3ced80aa9d', job_id='2fcd1c04-c1d3-4024-b60d-e4f96df50526', success=True, results=[ExperimentResult(shots=10000, success=True, meas_level=2, data=ExperimentResultData(counts={'0x4': 5058, '0x0': 4942}), header=QobjExperimentHeader(clbit_labels=[['c1', 0], ['c1', 1], ['c1', 2]], creg_sizes=[['c1', 3]], global_phase=6.283184508154124, memory_slots=3, metadata={}, n_qubits=3, name="(('S0', 'S0', 'S0'), ('Z', 'Z', 'Z'))", qreg_sizes=[['q', 3]], qubit_labels=[['q', 0], ['q', 1], ['q', 2]]), status=DONE, seed_simulator=3512995464, metadata={'parallel_state_update': 8, 'parallel_shots': 1, 'sample_measure_time': 0.003233781, 'noise': 'ideal', 'batched_shots_optimization': False, 'remapped_qubits': False, 'device': 'CPU', 'active_input_qubits': [0, 1, 2], 'measure_sampling': True, 'num_clbits': 3, 'input_qubit_map': [[2, 2], [1, 1], [0, 0]], 'num_qubits': 3, 'method': 'statevector', 'fusion': {'

In [70]:
# from qiskit.providers.ibmq.managed import IBMQJobManager
# job_manager = IBMQJobManager()

In [71]:
# job_set = job_manager.retrieve_job_set(job_set_id='973c2fdceaf547389a770d19aad463d8-1669966038684177', provider=provider)

In [72]:
# managed_results = job_set.results()

In [73]:
# frag_datas1_copy = frag_datas[1].copy()

In [78]:
frag_datas[0] = [frag_datas[0][0].combine_results()]

AttributeError: Attribute combine_results is not defined

In [75]:
# frag_datas[0] = run_circuits(multi_exp_circuits[0], initial_layout = None,
#                              backend = simulation_backend, shots = shots // total_variants,
#                              optimization_level = 3, monitor_jobs = True, noise_model = None)

In [79]:
frag_datas[0][0].results[0].header.name

"(('S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0'), ('Z', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z'))"

In [80]:
num_tomo_circuits

76

In [81]:
test = [[], []]

In [82]:
results_list = [[], []]
counts_list = [[], []] 
for i in range(0, num_fragments): 
    for j in range(0, num_tomo_circuits):
        start_idx = j * 12
        end_idx = (j + 1) * 12
        results_list[i].append(frag_datas[i][0].results[start_idx : end_idx])
        counts_list[i].append(frag_datas[i][0].get_counts()[start_idx : end_idx])


In [83]:
from mlrecon_methods import organize_tomography_data_from_list
organized_data = []
for i in range(0, num_tomo_circuits):
    frag_data = []
    frag_targets = ml.identify_frag_targets(wire_path_map_list[i])
    for j in range(0, num_fragments):
        frag_data.append(organize_tomography_data_from_list(results_list[j][i], counts_list[j][i],
                                              frag_targets[j].get("prep"),
                                              frag_targets[j].get("meas"),
                                              prep_basis = "SIC", extra_qc = []))
    organized_data.append(frag_data)

(('S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0'), ('Z', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z')) ('S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0') ('Z', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z')
(('S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0'), ('Z', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z')) ('S0',) ('Z',) [5] [5]
(('S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0'), ('Z', 'Z', 'Z', 'Z', 'Z', 'X', 'Z', 'Z')) ('S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0') ('Z', 'Z', 'Z', 'Z', 'Z', 'X', 'Z', 'Z')
(('S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0'), ('Z', 'Z', 'Z', 'Z', 'Z', 'X', 'Z', 'Z')) ('S0',) ('X',) [5] [5]
(('S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0'), ('Z', 'Z', 'Z', 'Z', 'Z', 'Y', 'Z', 'Z')) ('S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0') ('Z', 'Z', 'Z', 'Z', 'Z', 'Y', 'Z', 'Z')
(('S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0'), ('Z', 'Z', 'Z', 'Z', 'Z', 'Y', 'Z', 'Z')) ('S0',) ('Y',) [5] [5]
(('S0', 'S0', 'S0', 'S0', 'S0', 'S1', 'S0', 'S0'), ('Z', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z')) ('S0', 'S0

(('S0', 'S0', 'S0'), ('Z', 'Z', 'Z')) ('S0', 'S0', 'S0') ('Z', 'Z', 'Z')
(('S0', 'S0', 'S0'), ('Z', 'Z', 'Z')) ('S0',) ('Z',) [2] [1]
(('S0', 'S0', 'S0'), ('Z', 'X', 'Z')) ('S0', 'S0', 'S0') ('Z', 'X', 'Z')
(('S0', 'S0', 'S0'), ('Z', 'X', 'Z')) ('S0',) ('X',) [2] [1]
(('S0', 'S0', 'S0'), ('Z', 'Y', 'Z')) ('S0', 'S0', 'S0') ('Z', 'Y', 'Z')
(('S0', 'S0', 'S0'), ('Z', 'Y', 'Z')) ('S0',) ('Y',) [2] [1]
(('S0', 'S0', 'S1'), ('Z', 'Z', 'Z')) ('S0', 'S0', 'S1') ('Z', 'Z', 'Z')
(('S0', 'S0', 'S1'), ('Z', 'Z', 'Z')) ('S1',) ('Z',) [2] [1]
(('S0', 'S0', 'S1'), ('Z', 'X', 'Z')) ('S0', 'S0', 'S1') ('Z', 'X', 'Z')
(('S0', 'S0', 'S1'), ('Z', 'X', 'Z')) ('S1',) ('X',) [2] [1]
(('S0', 'S0', 'S1'), ('Z', 'Y', 'Z')) ('S0', 'S0', 'S1') ('Z', 'Y', 'Z')
(('S0', 'S0', 'S1'), ('Z', 'Y', 'Z')) ('S1',) ('Y',) [2] [1]
(('S0', 'S0', 'S2'), ('Z', 'Z', 'Z')) ('S0', 'S0', 'S2') ('Z', 'Z', 'Z')
(('S0', 'S0', 'S2'), ('Z', 'Z', 'Z')) ('S2',) ('Z',) [2] [1]
(('S0', 'S0', 'S2'), ('Z', 'X', 'Z')) ('S0', 'S0', 'S2') ('Z',

(('S0', 'S0', 'S0', 'S0', 'S0', 'S1', 'S0', 'S0'), ('Z', 'Z', 'Z', 'Z', 'Z', 'X', 'Z', 'Z')) ('S0', 'S0', 'S0', 'S0', 'S0', 'S1', 'S0', 'S0') ('Z', 'Z', 'Z', 'Z', 'Z', 'X', 'Z', 'Z')
(('S0', 'S0', 'S0', 'S0', 'S0', 'S1', 'S0', 'S0'), ('Z', 'Z', 'Z', 'Z', 'Z', 'X', 'Z', 'Z')) ('S1',) ('X',) [5] [5]
(('S0', 'S0', 'S0', 'S0', 'S0', 'S1', 'S0', 'S0'), ('Z', 'Z', 'Z', 'Z', 'Z', 'Y', 'Z', 'Z')) ('S0', 'S0', 'S0', 'S0', 'S0', 'S1', 'S0', 'S0') ('Z', 'Z', 'Z', 'Z', 'Z', 'Y', 'Z', 'Z')
(('S0', 'S0', 'S0', 'S0', 'S0', 'S1', 'S0', 'S0'), ('Z', 'Z', 'Z', 'Z', 'Z', 'Y', 'Z', 'Z')) ('S1',) ('Y',) [5] [5]
(('S0', 'S0', 'S0', 'S0', 'S0', 'S2', 'S0', 'S0'), ('Z', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z')) ('S0', 'S0', 'S0', 'S0', 'S0', 'S2', 'S0', 'S0') ('Z', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z')
(('S0', 'S0', 'S0', 'S0', 'S0', 'S2', 'S0', 'S0'), ('Z', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z')) ('S2',) ('Z',) [5] [5]
(('S0', 'S0', 'S0', 'S0', 'S0', 'S2', 'S0', 'S0'), ('Z', 'Z', 'Z', 'Z', 'Z', 'X', 'Z', 'Z')) ('S0', 'S0

(('S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0'), ('Z', 'Z', 'Z', 'Z', 'Z', 'Y', 'Z', 'Z')) ('S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0') ('Z', 'Z', 'Z', 'Z', 'Z', 'Y', 'Z', 'Z')
(('S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0', 'S0'), ('Z', 'Z', 'Z', 'Z', 'Z', 'Y', 'Z', 'Z')) ('S0',) ('Y',) [5] [5]
(('S0', 'S0', 'S0', 'S0', 'S0', 'S1', 'S0', 'S0'), ('Z', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z')) ('S0', 'S0', 'S0', 'S0', 'S0', 'S1', 'S0', 'S0') ('Z', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z')
(('S0', 'S0', 'S0', 'S0', 'S0', 'S1', 'S0', 'S0'), ('Z', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z', 'Z')) ('S1',) ('Z',) [5] [5]
(('S0', 'S0', 'S0', 'S0', 'S0', 'S1', 'S0', 'S0'), ('Z', 'Z', 'Z', 'Z', 'Z', 'X', 'Z', 'Z')) ('S0', 'S0', 'S0', 'S0', 'S0', 'S1', 'S0', 'S0') ('Z', 'Z', 'Z', 'Z', 'Z', 'X', 'Z', 'Z')
(('S0', 'S0', 'S0', 'S0', 'S0', 'S1', 'S0', 'S0'), ('Z', 'Z', 'Z', 'Z', 'Z', 'X', 'Z', 'Z')) ('S1',) ('X',) [5] [5]
(('S0', 'S0', 'S0', 'S0', 'S0', 'S1', 'S0', 'S0'), ('Z', 'Z', 'Z', 'Z', 'Z', 'Y', 'Z', 'Z')) ('S0', 'S0

In [84]:
for final_bits, fixed_bit_data in frag_data[0].items():
    prep_meas_states, state_counts = zip(*fixed_bit_data.items())
    prep_labels, meas_labels = zip(*prep_meas_states)
    prep_qubit_num = len(prep_labels[0])
    meas_qubit_num = len(meas_labels[0])
    print(prep_qubit_num)

1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1


In [85]:
len(organized_data)

76

In [86]:
recombined_lists = []
filtered_recombined_lists = []
norm_filtered_lists = []
for i in range(0, num_tomo_circuits):
    direct_models = ml.direct_fragment_model(organized_data[i])
    likely_models = ml.maximum_likelihood_model(direct_models)

    direct_recombined_dist = ml.recombine_fragment_models(direct_models, wire_path_map_list[i])
    likely_recombined_dist = ml.recombine_fragment_models(likely_models, wire_path_map_list[i])
    recombined_lists.append(likely_recombined_dist)
    filtered_recombined_lists.append(filter_results(likely_recombined_dist, [0]))
    norm_filtered_lists.append(norm_dict(filter_results(likely_recombined_dist, [0])))

{'0000000': {(('S0',), ('Zp',)): 65, (('S0',), ('Zm',)): 3, (('S0',), ('Xp',)): 44, (('S0',), ('Xm',)): 31, (('S0',), ('Yp',)): 35, (('S0',), ('Ym',)): 29, (('S1',), ('Zp',)): 29, (('S1',), ('Zm',)): 65, (('S1',), ('Xp',)): 31, (('S1',), ('Xm',)): 46, (('S1',), ('Yp',)): 73, (('S1',), ('Ym',)): 15, (('S2',), ('Zp',)): 18, (('S2',), ('Zm',)): 52, (('S2',), ('Xp',)): 64, (('S2',), ('Xm',)): 14, (('S2',), ('Yp',)): 32, (('S2',), ('Ym',)): 39, (('S3',), ('Zp',)): 23, (('S3',), ('Zm',)): 58, (('S3',), ('Xp',)): 29, (('S3',), ('Xm',)): 62, (('S3',), ('Yp',)): 15, (('S3',), ('Ym',)): 66}, '0000001': {(('S0',), ('Zp',)): 66, (('S0',), ('Zm',)): 2, (('S0',), ('Xp',)): 28, (('S0',), ('Xm',)): 29, (('S0',), ('Yp',)): 43, (('S0',), ('Ym',)): 46, (('S1',), ('Zp',)): 21, (('S1',), ('Zm',)): 68, (('S1',), ('Xp',)): 41, (('S1',), ('Xm',)): 59, (('S1',), ('Yp',)): 75, (('S1',), ('Ym',)): 13, (('S2',), ('Zp',)): 28, (('S2',), ('Zm',)): 76, (('S2',), ('Xp',)): 79, (('S2',), ('Xm',)): 12, (('S2',), ('Yp',

{'10': {(('S0',), ('Zp',)): 5058, (('S0',), ('Xm',)): 2477, (('S0',), ('Xp',)): 2434, (('S0',), ('Ym',)): 2517, (('S0',), ('Yp',)): 2488, (('S1',), ('Zp',)): 1691, (('S1',), ('Xp',)): 842, (('S1',), ('Xm',)): 859, (('S1',), ('Ym',)): 781, (('S1',), ('Yp',)): 813, (('S2',), ('Zp',)): 1676, (('S2',), ('Xp',)): 821, (('S2',), ('Xm',)): 815, (('S2',), ('Ym',)): 847, (('S2',), ('Yp',)): 809, (('S3',), ('Zp',)): 1638, (('S3',), ('Xm',)): 855, (('S3',), ('Xp',)): 853, (('S3',), ('Ym',)): 882, (('S3',), ('Yp',)): 804, (('S0',), ('Zm',)): 0, (('S1',), ('Zm',)): 0, (('S2',), ('Zm',)): 0, (('S3',), ('Zm',)): 0}, '00': {(('S0',), ('Zp',)): 4942, (('S0',), ('Xm',)): 2552, (('S0',), ('Xp',)): 2537, (('S0',), ('Yp',)): 2562, (('S0',), ('Ym',)): 2433, (('S1',), ('Zp',)): 1670, (('S1',), ('Xm',)): 789, (('S1',), ('Xp',)): 838, (('S1',), ('Ym',)): 807, (('S1',), ('Yp',)): 898, (('S2',), ('Zp',)): 1679, (('S2',), ('Xm',)): 800, (('S2',), ('Xp',)): 854, (('S2',), ('Yp',)): 855, (('S2',), ('Ym',)): 854, ((

{'00': {(('S0',), ('Zp',)): 5050, (('S0',), ('Xm',)): 2515, (('S0',), ('Xp',)): 2533, (('S0',), ('Ym',)): 2566, (('S0',), ('Yp',)): 2512, (('S1',), ('Zp',)): 1635, (('S1',), ('Xm',)): 848, (('S1',), ('Xp',)): 840, (('S1',), ('Ym',)): 858, (('S1',), ('Yp',)): 818, (('S2',), ('Zp',)): 1621, (('S2',), ('Xp',)): 843, (('S2',), ('Xm',)): 831, (('S2',), ('Ym',)): 843, (('S2',), ('Yp',)): 823, (('S3',), ('Zp',)): 1648, (('S3',), ('Xp',)): 850, (('S3',), ('Xm',)): 840, (('S3',), ('Yp',)): 827, (('S3',), ('Ym',)): 822, (('S0',), ('Zm',)): 0, (('S1',), ('Zm',)): 0, (('S2',), ('Zm',)): 0, (('S3',), ('Zm',)): 0}, '10': {(('S0',), ('Zp',)): 4950, (('S0',), ('Xp',)): 2443, (('S0',), ('Xm',)): 2509, (('S0',), ('Yp',)): 2467, (('S0',), ('Ym',)): 2455, (('S1',), ('Zp',)): 1678, (('S1',), ('Xm',)): 812, (('S1',), ('Xp',)): 857, (('S1',), ('Ym',)): 825, (('S1',), ('Yp',)): 827, (('S2',), ('Zp',)): 1739, (('S2',), ('Xm',)): 844, (('S2',), ('Xp',)): 811, (('S2',), ('Yp',)): 836, (('S2',), ('Ym',)): 811, ((

{'10': {(('S0',), ('Zp',)): 4944, (('S0',), ('Xp',)): 2499, (('S0',), ('Xm',)): 2470, (('S0',), ('Yp',)): 2444, (('S0',), ('Ym',)): 2517, (('S1',), ('Zp',)): 1672, (('S1',), ('Xp',)): 828, (('S1',), ('Xm',)): 833, (('S1',), ('Yp',)): 823, (('S1',), ('Ym',)): 843, (('S2',), ('Zp',)): 1640, (('S2',), ('Xp',)): 848, (('S2',), ('Xm',)): 858, (('S2',), ('Yp',)): 867, (('S2',), ('Ym',)): 863, (('S3',), ('Zp',)): 1685, (('S3',), ('Xm',)): 824, (('S3',), ('Xp',)): 826, (('S3',), ('Ym',)): 830, (('S3',), ('Yp',)): 844, (('S0',), ('Zm',)): 0, (('S1',), ('Zm',)): 0, (('S2',), ('Zm',)): 0, (('S3',), ('Zm',)): 0}, '00': {(('S0',), ('Zp',)): 5056, (('S0',), ('Xp',)): 2482, (('S0',), ('Xm',)): 2549, (('S0',), ('Ym',)): 2563, (('S0',), ('Yp',)): 2476, (('S1',), ('Zp',)): 1673, (('S1',), ('Xp',)): 877, (('S1',), ('Xm',)): 828, (('S1',), ('Ym',)): 775, (('S1',), ('Yp',)): 792, (('S2',), ('Zp',)): 1695, (('S2',), ('Xm',)): 845, (('S2',), ('Xp',)): 822, (('S2',), ('Ym',)): 798, (('S2',), ('Yp',)): 826, ((

{'0000000': {(('S0',), ('Zp',)): 9, (('S0',), ('Zm',)): 1, (('S0',), ('Xp',)): 5, (('S0',), ('Xm',)): 2, (('S0',), ('Yp',)): 2, (('S1',), ('Zp',)): 2, (('S1',), ('Zm',)): 8, (('S1',), ('Xp',)): 2, (('S1',), ('Xm',)): 8, (('S1',), ('Yp',)): 6, (('S1',), ('Ym',)): 2, (('S2',), ('Zp',)): 1, (('S2',), ('Zm',)): 5, (('S2',), ('Xp',)): 4, (('S2',), ('Yp',)): 6, (('S2',), ('Ym',)): 1, (('S3',), ('Zp',)): 1, (('S3',), ('Zm',)): 13, (('S3',), ('Xp',)): 1, (('S3',), ('Xm',)): 6, (('S3',), ('Yp',)): 2, (('S3',), ('Ym',)): 9, (('S0',), ('Ym',)): 0, (('S2',), ('Xm',)): 0}, '0000001': {(('S0',), ('Zp',)): 6, (('S0',), ('Xp',)): 1, (('S0',), ('Xm',)): 4, (('S0',), ('Yp',)): 4, (('S0',), ('Ym',)): 5, (('S1',), ('Zp',)): 2, (('S1',), ('Zm',)): 7, (('S1',), ('Xp',)): 3, (('S1',), ('Xm',)): 6, (('S1',), ('Yp',)): 13, (('S1',), ('Ym',)): 1, (('S2',), ('Zp',)): 2, (('S2',), ('Zm',)): 5, (('S2',), ('Xp',)): 4, (('S2',), ('Yp',)): 3, (('S2',), ('Ym',)): 4, (('S3',), ('Zp',)): 1, (('S3',), ('Zm',)): 10, (('S3

...

{'0000000': {(('S0',), ('Zp',)): 90, (('S0',), ('Zm',)): 1, (('S0',), ('Xp',)): 36, (('S0',), ('Xm',)): 42, (('S0',), ('Yp',)): 32, (('S0',), ('Ym',)): 43, (('S1',), ('Zp',)): 21, (('S1',), ('Zm',)): 70, (('S1',), ('Xp',)): 31, (('S1',), ('Xm',)): 49, (('S1',), ('Yp',)): 87, (('S1',), ('Ym',)): 18, (('S2',), ('Zp',)): 22, (('S2',), ('Zm',)): 55, (('S2',), ('Xp',)): 78, (('S2',), ('Xm',)): 13, (('S2',), ('Yp',)): 38, (('S2',), ('Ym',)): 43, (('S3',), ('Zp',)): 29, (('S3',), ('Zm',)): 60, (('S3',), ('Xp',)): 33, (('S3',), ('Xm',)): 76, (('S3',), ('Yp',)): 18, (('S3',), ('Ym',)): 72}, '0000001': {(('S0',), ('Zp',)): 78, (('S0',), ('Xp',)): 59, (('S0',), ('Xm',)): 33, (('S0',), ('Yp',)): 49, (('S0',), ('Ym',)): 39, (('S1',), ('Zp',)): 30, (('S1',), ('Zm',)): 66, (('S1',), ('Xp',)): 33, (('S1',), ('Xm',)): 56, (('S1',), ('Yp',)): 94, (('S1',), ('Ym',)): 24, (('S2',), ('Zp',)): 25, (('S2',), ('Zm',)): 62, (('S2',), ('Xp',)): 72, (('S2',), ('Xm',)): 8, (('S2',), ('Yp',)): 46, (('S2',), ('Ym',

{'0000000': {(('S0',), ('Zp',)): 77, (('S0',), ('Xp',)): 48, (('S0',), ('Xm',)): 49, (('S0',), ('Yp',)): 43, (('S0',), ('Ym',)): 55, (('S1',), ('Zp',)): 31, (('S1',), ('Zm',)): 30, (('S1',), ('Xp',)): 24, (('S1',), ('Xm',)): 44, (('S1',), ('Yp',)): 54, (('S1',), ('Ym',)): 8, (('S2',), ('Zp',)): 40, (('S2',), ('Zm',)): 40, (('S2',), ('Xp',)): 56, (('S2',), ('Xm',)): 5, (('S2',), ('Yp',)): 25, (('S2',), ('Ym',)): 32, (('S3',), ('Zp',)): 34, (('S3',), ('Zm',)): 33, (('S3',), ('Xp',)): 13, (('S3',), ('Xm',)): 34, (('S3',), ('Yp',)): 13, (('S3',), ('Ym',)): 52, (('S0',), ('Zm',)): 0}, '0000001': {(('S0',), ('Zp',)): 106, (('S0',), ('Zm',)): 1, (('S0',), ('Xp',)): 41, (('S0',), ('Xm',)): 44, (('S0',), ('Yp',)): 43, (('S0',), ('Ym',)): 38, (('S1',), ('Zp',)): 35, (('S1',), ('Zm',)): 31, (('S1',), ('Xp',)): 26, (('S1',), ('Xm',)): 37, (('S1',), ('Yp',)): 60, (('S1',), ('Ym',)): 8, (('S2',), ('Zp',)): 36, (('S2',), ('Zm',)): 30, (('S2',), ('Xp',)): 68, (('S2',), ('Xm',)): 8, (('S2',), ('Yp',)):

{'0000000': {(('S0',), ('Zp',)): 2, (('S1',), ('Zm',)): 1, (('S1',), ('Xm',)): 1, (('S2',), ('Zm',)): 1, (('S2',), ('Xp',)): 1, (('S2',), ('Ym',)): 1, (('S3',), ('Zm',)): 1, (('S3',), ('Xm',)): 2, (('S0',), ('Zm',)): 0, (('S0',), ('Xp',)): 0, (('S0',), ('Xm',)): 0, (('S0',), ('Yp',)): 0, (('S0',), ('Ym',)): 0, (('S1',), ('Zp',)): 0, (('S1',), ('Xp',)): 0, (('S1',), ('Yp',)): 0, (('S1',), ('Ym',)): 0, (('S2',), ('Zp',)): 0, (('S2',), ('Xm',)): 0, (('S2',), ('Yp',)): 0, (('S3',), ('Zp',)): 0, (('S3',), ('Xp',)): 0, (('S3',), ('Yp',)): 0, (('S3',), ('Ym',)): 0}, '0000001': {(('S0',), ('Zp',)): 16, (('S0',), ('Zm',)): 1, (('S0',), ('Xp',)): 13, (('S0',), ('Xm',)): 10, (('S0',), ('Yp',)): 7, (('S0',), ('Ym',)): 12, (('S1',), ('Zp',)): 11, (('S1',), ('Zm',)): 9, (('S1',), ('Xp',)): 3, (('S1',), ('Xm',)): 16, (('S1',), ('Yp',)): 3, (('S2',), ('Zp',)): 2, (('S2',), ('Zm',)): 12, (('S2',), ('Xp',)): 20, (('S2',), ('Xm',)): 2, (('S2',), ('Yp',)): 2, (('S2',), ('Ym',)): 1, (('S3',), ('Zp',)): 8, 

{'0010000': {(('S0',), ('Zp',)): 6, (('S0',), ('Xp',)): 4, (('S0',), ('Xm',)): 5, (('S0',), ('Yp',)): 6, (('S0',), ('Ym',)): 4, (('S1',), ('Zp',)): 4, (('S1',), ('Zm',)): 3, (('S1',), ('Xp',)): 4, (('S1',), ('Xm',)): 2, (('S1',), ('Yp',)): 7, (('S1',), ('Ym',)): 3, (('S2',), ('Zp',)): 5, (('S2',), ('Zm',)): 2, (('S2',), ('Xp',)): 7, (('S2',), ('Xm',)): 3, (('S2',), ('Yp',)): 8, (('S2',), ('Ym',)): 2, (('S3',), ('Zp',)): 2, (('S3',), ('Zm',)): 6, (('S3',), ('Xp',)): 7, (('S3',), ('Xm',)): 4, (('S3',), ('Yp',)): 5, (('S3',), ('Ym',)): 6, (('S0',), ('Zm',)): 0}, '0010001': {(('S0',), ('Zp',)): 4, (('S0',), ('Xp',)): 3, (('S0',), ('Xm',)): 5, (('S0',), ('Yp',)): 5, (('S0',), ('Ym',)): 5, (('S1',), ('Zp',)): 3, (('S1',), ('Zm',)): 8, (('S1',), ('Xp',)): 2, (('S1',), ('Xm',)): 9, (('S1',), ('Yp',)): 8, (('S1',), ('Ym',)): 3, (('S2',), ('Zp',)): 2, (('S2',), ('Zm',)): 6, (('S2',), ('Xp',)): 5, (('S2',), ('Xm',)): 5, (('S2',), ('Yp',)): 5, (('S2',), ('Ym',)): 5, (('S3',), ('Zp',)): 3, (('S3',)

{'00': {(('S0',), ('Zp',)): 10000, (('S0',), ('Xp',)): 5015, (('S0',), ('Xm',)): 4985, (('S0',), ('Yp',)): 5038, (('S0',), ('Ym',)): 4962, (('S1',), ('Zp',)): 3306, (('S1',), ('Xm',)): 1660, (('S1',), ('Xp',)): 1668, (('S1',), ('Yp',)): 1691, (('S1',), ('Ym',)): 1597, (('S2',), ('Zp',)): 3344, (('S2',), ('Xp',)): 1585, (('S2',), ('Xm',)): 1696, (('S2',), ('Ym',)): 1706, (('S2',), ('Yp',)): 1681, (('S3',), ('Zp',)): 3401, (('S3',), ('Xp',)): 1684, (('S3',), ('Xm',)): 1637, (('S3',), ('Yp',)): 1686, (('S3',), ('Ym',)): 1688, (('S0',), ('Zm',)): 0, (('S1',), ('Zm',)): 0, (('S2',), ('Zm',)): 0, (('S3',), ('Zm',)): 0}, '11': {(('S1',), ('Zp',)): 6694, (('S1',), ('Xm',)): 3293, (('S1',), ('Xp',)): 3379, (('S1',), ('Yp',)): 3321, (('S1',), ('Ym',)): 3391, (('S2',), ('Zp',)): 6656, (('S2',), ('Xp',)): 3360, (('S2',), ('Xm',)): 3359, (('S2',), ('Ym',)): 3229, (('S2',), ('Yp',)): 3384, (('S3',), ('Zp',)): 6599, (('S3',), ('Xm',)): 3387, (('S3',), ('Xp',)): 3292, (('S3',), ('Ym',)): 3255, (('S3',

In [87]:
# direct_models = ml.direct_fragment_model(frag_data)
# likely_models = ml.maximum_likelihood_model(direct_models)

# direct_recombined_dist = ml.recombine_fragment_models(direct_models, wire_path_map)
# likely_recombined_dist = ml.recombine_fragment_models(likely_models, wire_path_map)

In [88]:
from utils.utils import filter_results

In [89]:
filter_direct_recombined = filter_results(direct_recombined_dist, [0])

In [90]:

filter_likely_recombined = filter_results(likely_recombined_dist, [0])

In [91]:
norm_filter_dist = norm_dict(filter_likely_recombined)

In [92]:
final_expect_val = 0
for i in range(0, len(pauli_commute)):
    group = pauli_commute[i]
    for Pauli_tuple in group:
        coeff = Pauli_tuple[1]
        final_expect_val += coeff * evaluation(norm_filtered_lists[i], shots = total_counts(norm_filtered_lists[i]), Pauli = Pauli_tuple[0])  

In [93]:
final_expect_val

(-27.712038451777598+0j)

In [95]:
import json
with open('HF_auckland_check3.json', 'w') as f:
    json.dump(norm_filtered_lists, f)